In [1]:
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.document_loaders import PyPDFLoader

loader = PyPDFLoader("../data/raw/Constitution-of-Nepal.pdf")
documents = loader.load()

/home/suyog/Projects/nepal-legal-chatbot/.venv/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


Chunk the text

In [3]:
text_splitter = RecursiveCharacterTextSplitter(
    chunk_size = 1000,
    chunk_overlap= 200
)
chunks = text_splitter.split_documents(documents)
chunks

[Document(metadata={'producer': 'doPDF Ver 8.3 Build 931', 'creator': 'PyPDF', 'creationdate': '2015-11-01T10:54:39+05:45', 'source': '../data/raw/Constitution-of-Nepal.pdf', 'total_pages': 240, 'page': 0, 'page_label': '1'}, page_content='1 \n \n \n \n \n \nTHE CONSTITUTION OF NEPAL'),
 Document(metadata={'producer': 'doPDF Ver 8.3 Build 931', 'creator': 'PyPDF', 'creationdate': '2015-11-01T10:54:39+05:45', 'source': '../data/raw/Constitution-of-Nepal.pdf', 'total_pages': 240, 'page': 1, 'page_label': '2'}, page_content='2 \n \nTable of Contents \n \nPreamble   \nPart-1  \nPreliminary  \nPart-2  \nCitizenship  \nPart-3  \nFundamental Rights and Duties  \nPart-4  \nDirective Principles, Policies and Obligations of the State  \nPart-5  \nStructure of State and Distribution of State Power  \nPart -6  \nPresident and Vice-President  \nPart-7  \nFederal Executive  \nPart-8  \nFederal Legislature \nPart-9  \nFederal Legislative Procedures  \nPart-10  \nFederal Financial Procedures  \nPart-1

In [19]:
#length of chunks 
len(chunks)

474

# Generate Embeddings
Using Open-source embeddings, eg: sentence-transformers

In [5]:
from langchain.embeddings import HuggingFaceEmbeddings

embeddings_model = HuggingFaceEmbeddings(model_name = "all-MiniLM-L6-v2")

In [7]:
embeddings = [embeddings_model.embed_documents(chunk.page_content) for chunk in chunks]

In [20]:
embeddings[1]


[[-0.02816479653120041,
  -0.02478654310107231,
  -0.0906512439250946,
  0.04615798220038414,
  -0.03430003672838211,
  -0.07164937257766724,
  0.09874618053436279,
  0.05291064456105232,
  -0.004654154181480408,
  -0.05686270445585251,
  -0.02781936340034008,
  -0.1366634964942932,
  0.004582162946462631,
  -0.03427983075380325,
  -0.013689606450498104,
  0.10034561157226562,
  -0.11418325453996658,
  -0.030056055635213852,
  -0.029333272948861122,
  -0.06143577769398689,
  0.022478818893432617,
  -0.020646503195166588,
  0.05151907354593277,
  -0.00963179487735033,
  -0.07607568800449371,
  0.007215204648673534,
  -0.01874377764761448,
  0.04271319508552551,
  -0.007576633244752884,
  -0.10381785780191422,
  0.016248764470219612,
  -0.016131380572915077,
  -0.003352825529873371,
  -0.054221153259277344,
  0.026931576430797577,
  -0.09003175050020218,
  0.017826586961746216,
  -0.034206658601760864,
  -0.03024550899863243,
  0.050493091344833374,
  0.012781363911926746,
  -0.074230693

# Store Embeddings in a Vector Store(FAISS)

In [ ]:
from langchain.vectorstores import FAISS

vector_store = FAISS.from_documents(chunks,embeddings_model)
vector_store.save_local("faiss_index") #stores locally

# Query the Documents with LLaMA

In [26]:
from langchain.chains import RetrievalQA

qa = RetrievalQA.from_chain_type(
    llm = llm,
    chain_type="stuff",
    retriever = vector_store.as_retriever()

)

NameError: name 'llm' is not defined

In [ ]:
query = "Explain the article 4"
answer = qa.run(query)
answer